In [1]:
import librosa
import matplotlib.pyplot as plt
import IPython.display as ipd
import numpy as np
import pandas as pd

In [2]:
# feature names are initialized
features = ["harmonic_mean", "harmonic_var", "percussive_mean", "percussive_var", 
            "rms_mean", "rms_var", 
            "spec_second_mean", "spec_second_var", "spec_third_mean", "spec_third_var", "spec_fourth_mean", "spec_fourth_var"];

for i in range(1, 21):
  feature_name = "mfcc" + str(i) + "_mean"
  features.append(feature_name)

for i in range(1, 21):
  feature_name = "mfcc" + str(i) + "_var"
  features.append(feature_name)

X = pd.read_csv("extracted_features/recommender/data.txt", names=features) # data points are read
y = pd.read_csv("extracted_features/recommender/y.txt", names=range(1, 1001)); # data target labels are read
y = y.transpose()

print(X.shape, y.shape)
X.head()

(1000, 52) (1000, 1)


harmonic_mean  harmonic_var  percussive_mean  percussive_var  rms_mean  \
0       0.000033      0.013656         0.000330        0.003486  0.563806   
1       0.000476      0.016595         0.000518        0.002004  0.540435   
2      -0.000163      0.016543        -0.000268        0.004633  0.588423   
3       0.000031      0.016952        -0.000104        0.001813  0.534345   
4       0.000114      0.006187        -0.000012        0.001507  0.537805   

    rms_var  spec_second_mean  spec_second_var  spec_third_mean  \
0  0.078948      33680.954503     1.128636e+08         1.773840   
1  0.104708      35164.654938     2.544442e+08         2.245021   
2  0.050648      25625.525443     8.416998e+07         2.225454   
3  0.111438      22318.481580     1.242148e+08         3.247749   
4  0.107858      25740.695941     9.722850e+07         2.012868   

   spec_third_var  ...  mfcc11_var  mfcc12_var  mfcc13_var  mfcc14_var  \
0        0.201149  ...   38.205821   38.270407   31.941718   33.758050   
1        0.828744  ...   43.022364   51.437401   43.785227   40.777942   
2        0.459023  ...   43.948866   48.251983   43.211023   34.675321   
3        1.241887  ...   58.349657   41.591428   36.386798   29.266951   
4        0.818298  ...   43.553411   42.586570   41.851272   41.111907   

   mfcc15_var  mfcc16_var  mfcc17_var  mfcc18_var  mfcc19_var  mfcc20_var  
0   31.906852   35.416081   34.731329   37.898421   30.602889   32.291942  
1   33.001429   37.395107   38.419952   41.217259   30.989519   33.996483  
2   34.501859   29.404089   28.175414   31.298060   29.623310   29.823241  
3   44.090713   27.633107   30.182088   31.985474   28.845730   24.563945  
4   64.879078   44.235949   55.176918   50.945027   49.124910   46.473739  

[5 rows x 52 columns]

In [3]:
from sklearn.metrics.pairwise import cosine_similarity
from sklearn import preprocessing

scaler = preprocessing.StandardScaler()
X_scaled = scaler.fit_transform(X)

X_scaled = preprocessing.scale(X_scaled)
X_scaled.shape

(1000, 52)

In [4]:
# Cosine similarity
similarity = cosine_similarity(X_scaled)
print("Similarity shape:", similarity.shape)

# Convert into a dataframe and then set the row index and column names as labels
similarity_df = pd.DataFrame(similarity)
similarity_df = similarity_df.set_index(y.index)
similarity_df.columns = y.index

similarity_df.head()

Similarity shape: (1000, 1000)


1         2         3         4         5         6         7     \
1  1.000000  0.248292  0.515886  0.049475  0.150898 -0.228572 -0.225152   
2  0.248292  1.000000  0.158677  0.378267  0.172999  0.269733  0.401926   
3  0.515886  0.158677  1.000000  0.199680  0.393114  0.077947  0.127912   
4  0.049475  0.378267  0.199680  1.000000  0.026736  0.076193  0.215766   
5  0.150898  0.172999  0.393114  0.026736  1.000000  0.622847  0.438621   

       8         9         10    ...      991       992       993       994   \
1 -0.117487  0.513466 -0.027462  ... -0.104872  0.681322  0.746085  0.532474   
2  0.420695  0.211839  0.372605  ... -0.230773 -0.126505 -0.165927 -0.244623   
3  0.325044  0.419129 -0.124536  ... -0.045626  0.499463  0.544998  0.531318   
4  0.141998  0.122127 -0.051372  ... -0.216941 -0.101753 -0.160092 -0.056907   
5  0.491580  0.012003  0.485862  ...  0.119366  0.028044  0.115280  0.067564   

       995       996       997       998       999       1000  
1  0.596768  0.585685  0.678663  0.600131  0.190153  0.238831  
2 -0.196019 -0.123126 -0.138835 -0.178500  0.250059  0.202961  
3  0.500931  0.450736  0.495953  0.533121  0.284208  0.309003  
4 -0.093326 -0.063542  0.042561 -0.106820  0.356812  0.393374  
5 -0.037877  0.052069  0.007045  0.117258 -0.003887 -0.081652  

[5 rows x 1000 columns]

In [5]:
# find the most similar songs to this song:
track, sr = librosa.load("data/genre_data/pop/pop.00019.wav")
ipd.Audio(track, rate=sr)

In [6]:
# top three most similar songs
track_idx = 720
top3 = similarity_df[track_idx].sort_values(ascending=False)[1:4]
top3 

724    0.834363
735    0.809479
792    0.795371
Name: 720, dtype: float64

In [7]:
# most similar song
track, sr = librosa.load("data/genre_data/pop/pop.00023.wav")
ipd.Audio(track, rate=sr)

In [8]:
# second most similar song
track, sr = librosa.load("data/genre_data/pop/pop.00034.wav")
ipd.Audio(track, rate=sr)

In [9]:
# third most similar song
track, sr = librosa.load("data/genre_data/pop/pop.00091.wav")
ipd.Audio(track, rate=sr)